# Лабораторная работа № 4

## Постановка задачи

- Реализовать алгоритм базовой модели Идена; 
- Визуализировать рост кластера; 
- В лог-лог масштабе построить зависимости $N(R_{g})$ и $N_s(R_{g})$; 
- Определить размерность $d$ и $d_s$;
- Реализовать алгоритм модели экранированного роста;
- Определить размерность кластера $d$ для случаев: $\psi < 2$, $\psi = 2$ и $\psi > 2$.

## Реализация алгоритма базовой модели Идена

### Описание

Рост кластера имитируется последовательным заполнением узлов квадратной решетки по периметру кластера.

В начальный момент времени кластер состоит всего из одной частицы ("зерна" роста). В дальнейшим рост кластера происходит за счет последовательного присоединения новых частиц в узлах по его периметру.

### Структура кластеров Идена

Зависимость количества частиц в кластере и его радиусом гирации $R_g$ описывается соотношением $N \sim R_g^d$, где величина $d$ практически совпадает с евклидовой размерностью.

Радиус гирации определяется, как $R_g = \sqrt{ \dfrac{1}{N} \sum\limits_{i=1}^{N} (\vec{r}_i - \vec{r})^2}$, где $\vec{r} = \dfrac{1}{N}\sum\limits_{i=1}^{N} \vec{r}_i$ соответствует координатам центра масс кластера.

Поверхность кластеров Идена имеет фрактальные свойства, а число узлов на периметре растет как $N_s \sim R_g^{d_s}$, где $d_s > 1$ $-$ фрактальная размерность периметра.

Алгоритм *базовой модели Идена* и *модели экранированного роста* были реализованы в отдельном модуле [IdenCluster.py](https://github.com/AlexeyMakurin/Computer-technologies-in-physics/blob/main/IdenCluster.py). Здесь представлены результаты его работы.

In [112]:
import IdenCluster
import plotly.graph_objects as go
import numpy as np

from plotly.subplots import make_subplots

Создание кластера базовой модели с сеткой размером $n \times n$ с "зерном" роста в центре.

In [2]:
n=31
cluster = IdenCluster.BasicModel(n)

Запуск роста кластера.

In [28]:
cluster.growth(frame=10)

Параметор frame включает запись стадий роста кластера для создания анимации (по умолчанию frame=0), значение параметра означает, сколько новых частиц будет содержать один кадр анимации.

Построение анимации.

In [29]:
cluster.vizualization()

Цвет кластера меняется синусоидально, параметром, определяющим значение цвета частицы, является растояния между "зерном" роста и положением частицы в кластере.

Создадим новый кластер, и визуализируем его, но без демонстрации роста. В этом случае параметр frame не указывается. 

In [135]:
new_cluster = IdenCluster.BasicModel(101)
new_cluster.growth(R_g=True)
new_cluster.vizualization()

Параметр R_g (по умолчанию False) отвечает за запись изменения радиуса гирации кластера.

Построим зависимости $N(R_{g})$ и $N_s(R_{g})$ в лог-лог масштабе.

In [136]:
r_g = new_cluster.radius_g
p_count = new_cluster.particles_count
n_count = new_cluster.count_node

Также определим закон зависимостей как $N(R_g) \approx \beta R_g ^{\alpha}$, значение коэфициентов найдем с помощью метода наименьших квадратов.

In [137]:
def least_square_method(x, y):
    A = np.vstack([np.log(x), np.ones(len(x))]).T
    alpha, beta = np.linalg.lstsq(A, np.log(y), rcond=None)[0]

    return alpha, np.exp(beta)

In [138]:
# Метод наименьших квадратов
a_1, b_1 = least_square_method(r_g, p_count)
a_2, b_2 = least_square_method(r_g, n_count)

print(f"Для числа частиц:\nalpha = {a_1}\nbeta = {b_1}\n")
print(f"Для числа узлов периметра:\nalpha = {a_2}\nbeta = {b_2}")

Для числа частиц:
alpha = 2.0880204570717282
beta = 4.558411660642605

Для числа узлов периметра:
alpha = 1.2525398547130706
beta = 8.333263029115336


In [139]:
fig = make_subplots(rows=2, cols=1, subplot_titles=(
    'Зависимость числа частиц в кластере от значения радиуса гирации', 
    "Зависимость числа узлов в периметре кластера от значения радиуса гирации"
))

fig.add_trace(go.Scatter(x=r_g[0:-1:5], y=p_count[0:-1:5], mode='markers', name='$R_{g}$'), row=1, col=1)
fig.add_trace(go.Scatter(x=r_g, y=b_1 * r_g**a_1, mode='lines', name='$N(R_g) = betaN^{alpha}$'), row=1, col=1)

fig.add_trace(go.Scatter(x=r_g[0:-1:5], y=n_count[0:-1:5], mode='markers', name='$R_{g}$'), row=2, col=1)
fig.add_trace(go.Scatter(x=r_g, y=b_2 * r_g**a_2, mode='lines', name='$N_s(R_g) = betaN_s^{alpha}$'), row=2, col=1)


fig.update_yaxes(type="log", title='$N$', row=1)
fig.update_yaxes(type="log", title='$N_s$', row=2)

fig.update_xaxes(title='$R_g$', type="log")
fig.show()

Полученные коэффициенты $\alpha$ для зависимостей $N$ и $N_s$ являются размерностями $d$ и $d_s$ соответственно.

Размерность кластера $d$ примерно совпадает с евклидовой размерностью, в даном случае евклидова размерность равна $2$. Полученное значение $d \approx 2$.

In [140]:
print(f'Размерность кластера: {a_1}')

Размерность кластера: 2.0880204570717282


Фрактальная размерность периметра $d_s > 1$:

In [142]:
print(f'Фрактальная размерность периметра: {a_2}')

Фрактальная размерность периметра: 1.2525398547130706


## Модель экранированного роста

Частицы и класттеры имеют "заряд" и учитывается отталкивание между кластером и присоединяющейся частицей.

Вероятность роста на периметре $f_i$ определяется выражением

$$ f_i = \prod\limits_{j=1}^{N} \exp\Bigl(-\dfrac{a}{r^{\psi}_{ij}} \Bigr)  \Big/  \sum^{N_s}_{i=1} \prod^N_{j=1} \exp\Bigl(-\dfrac{a}{r^{\psi}_{ij}} \Bigr),$$

где $N$, $N_s$ $-$ число частиц в кластере и число узлов на периметре, $r_{ij}$ $-$ расстояние между занятым $(j)$ и узлом на периметре $(i)$; $a$, $\psi$ $-$ параметры, характеризующие потенциал взаимодействия.

Визуализация роста кластера.

In [151]:
screened_cluster = IdenCluster.ScreenedGrowthModel(40, a=1, psi=2)
screened_cluster.growth(frame=12)
screened_cluster.vizualization()

10% 15% 20% 25% 30% 35% 40% 45% 50% 55% 60% 65% 70% 75% 80% 85% 90% 95% 100% 

### Размерность $d$ для случая $\psi < 2$

Пусть $\psi = 1$, тогда кластер примет следующий вид

In [147]:
screened_cluster = IdenCluster.ScreenedGrowthModel(121, a=1, psi=1)
screened_cluster.growth(R_g=True)
screened_cluster.vizualization()

3% 5% 6% 8% 10% 11% 13% 15% 16% 18% 20% 21% 23% 25% 26% 28% 30% 31% 33% 35% 36% 38% 40% 41% 43% 45% 46% 48% 50% 51% 53% 55% 56% 58% 60% 61% 63% 65% 66% 68% 70% 71% 73% 75% 76% 78% 80% 81% 83% 85% 86% 88% 90% 91% 93% 95% 96% 98% 100% 

Нахождение размерности $d$

In [148]:
r_g_1 = screened_cluster.radius_g
p_count_1 = screened_cluster.particles_count

In [150]:
a_s_1 = least_square_method(r_g_1, p_count_1)[0]

print(f"Размерность кластера для psi < 2: {a_s_1}")

Размерность кластера для psi < 2 = 1.2243778076409113


### Размерность $d$ для случая $\psi = 2$

In [153]:
screened_cluster = IdenCluster.ScreenedGrowthModel(121, a=1, psi=2)
screened_cluster.growth(R_g=True)
screened_cluster.vizualization()

3% 5% 6% 8% 10% 11% 13% 15% 16% 18% 20% 21% 23% 25% 26% 28% 30% 31% 33% 35% 36% 38% 40% 41% 43% 45% 46% 48% 50% 51% 53% 55% 56% 58% 60% 61% 63% 65% 66% 68% 70% 71% 73% 75% 76% 78% 80% 81% 83% 85% 86% 88% 90% 91% 93% 95% 96% 98% 100% 

In [157]:
r_g_2 = screened_cluster.radius_g
p_count_2 = screened_cluster.particles_count

# Метод наименьших квадратов
a_s_2 = least_square_method(r_g_2, p_count_2)[0]

print(f"Размерность кластера для psi = 2: {a_s_2}")

Размерность кластера для psi = 2: 1.7466533534041804


### Размерность $d$ для случая $\psi = 3$

In [158]:
screened_cluster = IdenCluster.ScreenedGrowthModel(121, a=1, psi=3)
screened_cluster.growth(R_g=True)
screened_cluster.vizualization()

3% 5% 6% 8% 10% 11% 13% 15% 16% 18% 20% 21% 23% 25% 26% 28% 30% 31% 33% 35% 36% 38% 40% 41% 43% 45% 46% 48% 50% 51% 53% 55% 56% 58% 60% 61% 63% 65% 66% 68% 70% 71% 73% 75% 76% 78% 80% 81% 83% 85% 86% 88% 90% 91% 93% 95% 96% 98% 100% 

In [159]:
r_g_3 = screened_cluster.radius_g
p_count_3 = screened_cluster.particles_count

# Метод наименьших квадратов
a_s_3 = least_square_method(r_g_3, p_count_3)[0]

print(f"Размерность кластера для psi = 3: {a_s_3}")

Размерность кластера для psi = 3: 2.1024817638894735
